###### Imports and Settings

In [1]:
import pandas as pd
import numpy as np
import requests
import geopandas as gpd
import folium
import branca
import branca.colormap as cm
pd.set_option('display.width', 150)

In [2]:
data = pd.read_csv('../data/joined.csv')

In [3]:
data.head()

County           GEOID   total  nothisp_whitealone  StateFIPS  CountyFIPS Region  minority  %minority  total55+  total65+  \
0     Stewart County, Tennessee  0500000US47161   13553               12397         47         161   GNRC      1156       8.53      4666      2678   
1  Montgomery County, Tennessee  0500000US47125  204992              128270         47         125   GNRC     76722      37.43     38586     19065   
2     Houston County, Tennessee  0500000US47083    8201                7521         47          83   GNRC       680       8.29      2874      1692   
3   Humphreys County, Tennessee  0500000US47085   18528               16915         47          85   GNRC      1613       8.71      6280      3593   
4     Dickson County, Tennessee  0500000US47043   53289               47624         47          43   GNRC      5665      10.63     15914      8513   

   total55+notminority  total65+notminority  minority55+  minority65+  %minority55+  %minority65+  
0                 4462                 2573          204          105          4.37          3.92  
1                28381                14869        10205         4196         26.45         22.01  
2                 2679                 1584          195          108          6.78          6.38  
3                 6115                 3528          165           65          2.63          1.81  
4                14896                 8121         1018          392          6.40          4.60

## Bring in geo

In [4]:
url= 'https://www2.census.gov/geo/tiger/TIGER2019/COUNTY/tl_2019_us_county.zip'
geo = gpd.read_file(url)
print('Your geographic file is ready.')

Your geographic file is ready.


In [5]:
geo.head()

STATEFP COUNTYFP  COUNTYNS  GEOID       NAME          NAMELSAD LSAD CLASSFP  MTFCC CSAFP CBSAFP METDIVFP FUNCSTAT       ALAND    AWATER  \
0      31      039  00835841  31039     Cuming     Cuming County   06      H1  G4020  None   None     None        A  1477652222  10690952   
1      53      069  01513275  53069  Wahkiakum  Wahkiakum County   06      H1  G4020  None   None     None        A   680962890  61582307   
2      35      011  00933054  35011    De Baca    De Baca County   06      H1  G4020  None   None     None        A  6016819475  29089486   
3      31      109  00835876  31109  Lancaster  Lancaster County   06      H1  G4020   339  30700     None        A  2169270569  22849484   
4      31      129  00835886  31129   Nuckolls   Nuckolls County   06      H1  G4020  None   None     None        A  1489645188   1718484   

      INTPTLAT      INTPTLON                                           geometry  
0  +41.9158651  -096.7885168  POLYGON ((-97.01952 42.00410, -97.01952 42.004...  
1  +46.2946377  -123.4244583  POLYGON ((-123.43639 46.23820, -123.44759 46.2...  
2  +34.3592729  -104.3686961  POLYGON ((-104.56739 33.99757, -104.56772 33.9...  
3  +40.7835474  -096.6886584  POLYGON ((-96.91075 40.78494, -96.91075 40.790...  
4  +40.1764918  -098.0468422  POLYGON ((-98.27367 40.08940, -98.27367 40.089...

In [6]:
geo = geo.drop(columns = ['COUNTYNS','NAME','NAMELSAD','LSAD','CLASSFP','MTFCC','CSAFP','CBSAFP','METDIVFP','FUNCSTAT',
                         'ALAND','AWATER','INTPTLAT','INTPTLON'])

In [7]:
geo = geo.loc[geo['STATEFP'] == '47']

In [8]:
geo.head()

STATEFP COUNTYFP  GEOID                                           geometry
29       47      065  47065  POLYGON ((-85.29254 35.26291, -85.29238 35.263...
64       47      115  47115  POLYGON ((-85.54387 35.30237, -85.54187 35.301...
67       47      185  47185  MULTIPOLYGON (((-85.64136 35.84077, -85.63987 ...
128      47      129  47129  POLYGON ((-84.79101 36.05853, -84.79184 36.059...
181      47      013  47013  POLYGON ((-84.32221 36.39287, -84.32249 36.393...

### Create appropriate GEOID in original df and join as gdf

In [9]:
data['GEOID'] = data['GEOID'].str.slice(start = 11)

In [10]:
data.head(2)

County GEOID   total  nothisp_whitealone  StateFIPS  CountyFIPS Region  minority  %minority  total55+  total65+  \
0     Stewart County, Tennessee   161   13553               12397         47         161   GNRC      1156       8.53      4666      2678   
1  Montgomery County, Tennessee   125  204992              128270         47         125   GNRC     76722      37.43     38586     19065   

   total55+notminority  total65+notminority  minority55+  minority65+  %minority55+  %minority65+  
0                 4462                 2573          204          105          4.37          3.92  
1                28381                14869        10205         4196         26.45         22.01

In [11]:
geo_df = pd.merge(geo, data, left_on = 'COUNTYFP', right_on = 'GEOID', how = 'inner',).reset_index(drop = True)

In [12]:
geo_df.head()

STATEFP COUNTYFP GEOID_x                                           geometry                        County GEOID_y   total  nothisp_whitealone  \
0      47      149   47149  POLYGON ((-86.61890 35.96814, -86.61890 35.968...  Rutherford County, Tennessee     149  324139              225604   
1      47      169   47169  POLYGON ((-86.26890 36.45044, -86.26890 36.450...   Trousdale County, Tennessee     169   10910                9007   
2      47      165   47165  POLYGON ((-86.69076 36.40974, -86.69082 36.409...      Sumner County, Tennessee     165  187680              155517   
3      47      161   47161  POLYGON ((-88.06146 36.44409, -88.06166 36.444...     Stewart County, Tennessee     161   13553               12397   
4      47      083   47083  POLYGON ((-87.75722 36.34264, -87.75652 36.342...     Houston County, Tennessee     083    8201                7521   

   StateFIPS  CountyFIPS  ... minority  %minority  total55+  total65+  total55+notminority  total65+notminority  minority55+  minority65+  \
0         47         149  ...    98535      30.40     68861     34063                56833                29282        12028         4781   
1         47         169  ...     1903      17.44      2641      1454                 2220                 1215          421          239   
2         47         165  ...    32163      17.14     54542     29889                49291                27401         5251         2488   
3         47         161  ...     1156       8.53      4666      2678                 4462                 2573          204          105   
4         47          83  ...      680       8.29      2874      1692                 2679                 1584          195          108   

   %minority55+  %minority65+  
0         17.47         14.04  
1         15.94         16.44  
2          9.63          8.32  
3          4.37          3.92  
4          6.78          6.38  

[5 rows x 21 columns]

In [13]:
print('minimum % minority is:',geo_df['%minority'].min(),   
      'maximum % minority is:',geo_df['%minority'].max())

minimum % minority is: 8.22 maximum % minority is: 43.99


In [14]:
print('minimum % minority 55+ is:',geo_df['%minority55+'].min(),   
      'maximum % minority 55+ is:',geo_df['%minority55+'].max())

minimum % minority 55+ is: 2.63 maximum % minority 55+ is: 32.18


In [15]:
print('minimum % minority 65+ is:',geo_df['%minority65+'].min(),   
      'maximum % minority 65+ is:',geo_df['%minority65+'].max())

minimum % minority 65+ is: 1.81 maximum % minority 65+ is: 27.91


## Create Folium Map

In [16]:
geo_df['id'] = geo_df.index.astype(str)

In [17]:
# myscale = (geo_df['%minority'].quantile((0,0.1,0.75,0.9,0.98,1))).tolist()

chor = folium.Choropleth(geo_data = geo_df, 
                        name = 'Choropleth', 
                        data = geo_df, 
                        columns = ['id','%minority'], 
                        key_on = 'feature.properties.id', 
                        fill_color = 'GnBu',
                        #threshold_scale = myscale,
                        fill_opacity = 0.8,
                        line_opacity = 0.2,
                        line_color = 'black',
                        line_weight = 1,
                        highlight = True,
                        overlay = True,
                        show = True,
                        smooth_factor = 1.0,
                        legend_name = 'Percent Minority')

chor2 = folium.Choropleth(geo_data = geo_df, 
                        name = 'Choropleth', 
                        data = geo_df, 
                        columns = ['id','%minority55+'], 
                        key_on = 'feature.properties.id', 
                        fill_color = 'GnBu',
                        #threshold_scale = myscale,
                        fill_opacity = 0.8,
                        line_opacity = 0.2,
                        line_color = 'black',
                        line_weight = 1,
                        highlight = True,
                        overlay = True,
                        show = True,
                        smooth_factor = 1.0,
                        legend_name = 'Percent Minority 55+')
chor3 = folium.Choropleth(geo_data = geo_df, 
                        name = 'Choropleth', 
                        data = geo_df, 
                        columns = ['id','%minority65+'], 
                        key_on = 'feature.properties.id', 
                        fill_color = 'GnBu',
                        #threshold_scale = myscale,
                        fill_opacity = 0.8,
                        line_opacity = 0.2,
                        line_color = 'black',
                        line_weight = 1,
                        highlight = True,
                        overlay = True,
                        show = True,
                        smooth_factor = 1.0,
                        legend_name = 'Percent Minority 65+')

In [18]:
geo_df.columns

Index(['STATEFP', 'COUNTYFP', 'GEOID_x', 'geometry', 'County', 'GEOID_y', 'total', 'nothisp_whitealone', 'StateFIPS', 'CountyFIPS', 'Region',
       'minority', '%minority', 'total55+', 'total65+', 'total55+notminority', 'total65+notminority', 'minority55+', 'minority65+', '%minority55+',
       '%minority65+', 'id'],
      dtype='object')

In [19]:
# Add hover functionality.
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

#tooltip as geojson layer
TT = folium.features.GeoJson(data = geo_df,
                             style_function=style_function, 
                             control=False,
                             highlight_function=highlight_function, 
                             tooltip=folium.features.GeoJsonTooltip(
                                 fields=['County', 'total', 'nothisp_whitealone', 'minority', '%minority'],
                                 aliases=['County:', 'Total Pop.:', 'Non-Minority Pop.:', 'Minority Pop.:', '% Minority:'],
                                 style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")))

TT2 = folium.features.GeoJson(data = geo_df,
                             style_function=style_function, 
                             control=False,
                             highlight_function=highlight_function, 
                             tooltip=folium.features.GeoJsonTooltip(
                                 fields=['County', 'total55+', 'total55+notminority', 'minority55+', '%minority55+'],
                                 aliases=['County:', 'Total Pop. 55+:', '55+ Non-Minority Pop.:', '55+ Minority Pop.:', '55+ % Minority:'],
                                 style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")))
TT3 = folium.features.GeoJson(data = geo_df,
                             style_function=style_function, 
                             control=False,
                             highlight_function=highlight_function, 
                             tooltip=folium.features.GeoJsonTooltip(
                                 fields=['County', 'total65+', 'total65+notminority', 'minority65+', '%minority65+'],
                                 aliases=['County:', 'Total Pop. 65+:', '65+ Non-Minority Pop.:', '65+ Minority Pop.:', '65+ % Minority:'],
                                 style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")))

## Visualization of the total minority population:

In [20]:
m = folium.Map(location = [36.326848, -87.069354], tiles = 'cartodbpositron', zoom_start = 9, control_scale = True)
m.add_child(chor)
m.add_child(TT)
m

## Visualization of the 55+ Minority Population:

In [21]:
m = folium.Map(location = [36.326848, -87.069354], tiles = 'cartodbpositron', zoom_start = 9, control_scale = True)
m.add_child(chor2)
m.add_child(TT2)
m

## Visualization of the 65+ Minority Population:

In [22]:
m = folium.Map(location = [36.326848, -87.069354], tiles = 'cartodbpositron', zoom_start = 9, control_scale = True)
m.add_child(chor3)
m.add_child(TT3)
m